In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install optuna
!pip install lightgbm==3.3.2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 380.1/380.1 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.0/233.0 kB 12.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 5.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 8.6 MB/s eta 0:00:00
  Attempting uninstall: lightgbm
    Found existing installation: lightgbm 4.4.0
    Uninstalling lightgbm-4.4.0:
      Successfully uninstalled lightgbm-4.4.0


In [ ]:
import numpy as np
import pandas as pd
import random
import os
import matplotlib.pyplot as plt
import seaborn as sns
from lightgbm import LGBMRegressor
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import StandardScaler
import optuna
import lightgbm as lgb
from sklearn.model_selection import train_test_split, KFold
from lightgbm import early_stopping
from sklearn.metrics import r2_score
import joblib
%matplotlib inline

def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)

seed_everything(42)

/usr/local/lib/python3.10/dist-packages/dask/dataframe/__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


In [ ]:
file_path_2022 = '/content/drive/MyDrive/library_seat_occupancy_2022.csv'
data_2022 = pd.read_csv(file_path_2022, encoding='cp949')

file_path_2023 = '/content/drive/MyDrive/practce/library_seat_occupancy_2023.csv'
data = pd.read_csv(file_path_2023, encoding='cp949')

file_path_2024 = '/content/drive/MyDrive/library_seat_occupancy_2024.csv'
data_2024 = pd.read_csv(file_path_2024, encoding='cp949')

#data = pd.concat([data_2022, data_2023, data_2024]).sort_values(by='datetime').reset_index(drop=True)

data.head()

datetime  1f_1  1f_but  2f_he  2f_2  1f_ele
0  2023-01-01 00:00:00    58      24     22    15       9
1  2023-01-01 01:00:00    31      13     23     7       8
2  2023-01-01 02:00:00    17      22     27     9       7
3  2023-01-01 03:00:00    15      15     23     9       6
4  2023-01-01 04:00:00    26      26     22     9       7

In [ ]:
data.tail()

datetime  1f_1  1f_but  2f_he  2f_2  1f_ele
8732  2023-12-30 20:00:00    95      56     85    40      10
8733  2023-12-30 21:00:00    87      55     72    23      12
8734  2023-12-30 22:00:00    70      42     28    25       9
8735  2023-12-30 23:00:00    47      46     27    37      10
8736  2023-12-31 00:00:00    49      49     39    25       7

In [ ]:
data['datetime'] = pd.to_datetime(data['datetime'])
data['year'] = data['datetime'].dt.year
data['month'] = data['datetime'].dt.month
data['day'] = data['datetime'].dt.day
data['hour'] = data['datetime'].dt.hour
data['dayofweek'] = data['datetime'].dt.dayofweek

X = data[['year', 'month', 'day', 'hour', 'dayofweek']]
target_columns = ['1f_1', '1f_but', '2f_he', '2f_2', '1f_ele']

data.head()

datetime  1f_1  1f_but  2f_he  2f_2  1f_ele  year  month  day  \
0 2023-01-01 00:00:00    58      24     22    15       9  2023      1    1   
1 2023-01-01 01:00:00    31      13     23     7       8  2023      1    1   
2 2023-01-01 02:00:00    17      22     27     9       7  2023      1    1   
3 2023-01-01 03:00:00    15      15     23     9       6  2023      1    1   
4 2023-01-01 04:00:00    26      26     22     9       7  2023      1    1   

   hour  dayofweek  
0     0          6  
1     1          6  
2     2          6  
3     3          6  
4     4          6

In [ ]:
def train_and_evaluate_model(target_column):
    y = data[target_column]

    X_train_full, X_test, y_train_full, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
    kfold = KFold(n_splits=5, shuffle=True, random_state=42)

    def objective(trial):
        param = {
            "objective": "regression",
            "metric": "rmse",
            "verbosity": -1,
            "boosting_type": "gbdt",
            "lambda_l1": trial.suggest_float("lambda_l1", 1e-8, 10.0),
            "lambda_l2": trial.suggest_float("lambda_l2", 1e-8, 10.0),
            "num_leaves": trial.suggest_int("num_leaves", 2, 256),
            "feature_fraction": trial.suggest_float("feature_fraction", 0.4, 1.0),
            "bagging_fraction": trial.suggest_float("bagging_fraction", 0.4, 1.0),
            "bagging_freq": trial.suggest_int("bagging_freq", 1, 7),
            "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
            "learning_rate": trial.suggest_float("learning_rate", 1e-4, 1e-1),
        }

        r2_scores = []

        for train_index, val_index in kfold.split(X_train_full):
            X_train, X_val = X_train_full.iloc[train_index], X_train_full.iloc[val_index]
            y_train, y_val = y_train_full.iloc[train_index], y_train_full.iloc[val_index]

            model = lgb.LGBMRegressor(**param)
            model.fit(X_train, y_train, eval_set=[(X_val, y_val)],
                      early_stopping_rounds=100, verbose=False)

            y_pred = model.predict(X_val)
            r2 = r2_score(y_val, y_pred)
            r2_scores.append(r2)

        return np.mean(r2_scores)

    study = optuna.create_study(direction="maximize")
    study.optimize(objective, n_trials=100)

    best_params = study.best_params
    print(f"Best params for {target_column}: {best_params}")

    model = lgb.LGBMRegressor(**best_params)
    model.fit(X_train_full, y_train_full)

    model_filename = f"{target_column}_model_final.pkl"
    joblib.dump(model, "/content/drive/MyDrive/practce/" + model_filename)
    print(f"Model saved as: /content/drive/MyDrive/practce/{model_filename}")

    y_test_pred = model.predict(X_test)
    test_r2 = r2_score(y_test, y_test_pred)
    print(f"Test R2 score for {target_column}: {test_r2}")

    future_prediction = model.predict(future_X)
    print(f"Future prediction for {target_column}: {future_prediction[0]}")

    return future_prediction[0]

future_predictions = {}
for target_column in target_columns:
    print(f"Training model for {target_column}")
    future_predictions[target_column] = train_and_evaluate_model(target_column)

[I 2024-08-28 02:24:15,493] A new study created in memory with name: no-name-b8979e8b-eb51-47f1-8370-a590c74fad24


Training model for 1f_1
[LightGBM] [Warning] feature_fraction is set=0.770150279456767, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.770150279456767
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] lambda_l2 is set=3.9692659066748037, reg_lambda=0.0 will be ignored. Current value: lambda_l2=3.9692659066748037
[LightGBM] [Warning] bagging_fraction is set=0.8702645753942929, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8702645753942929
[LightGBM] [Warning] lambda_l1 is set=2.3639511783118508, reg_alpha=0.0 will be ignored. Current value: lambda_l1=2.3639511783118508
[LightGBM] [Warning] feature_fraction is set=0.770150279456767, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.770150279456767
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] lambda_l2 is set=3.96

/usr/local/lib/python3.10/dist-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.10/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.10/dist-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is depre

[LightGBM] [Warning] feature_fraction is set=0.770150279456767, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.770150279456767
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] lambda_l2 is set=3.9692659066748037, reg_lambda=0.0 will be ignored. Current value: lambda_l2=3.9692659066748037
[LightGBM] [Warning] bagging_fraction is set=0.8702645753942929, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8702645753942929
[LightGBM] [Warning] lambda_l1 is set=2.3639511783118508, reg_alpha=0.0 will be ignored. Current value: lambda_l1=2.3639511783118508
[LightGBM] [Warning] feature_fraction is set=0.770150279456767, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.770150279456767
[LightGBM] [Warning] bagging_freq is set=3, subsample_freq=0 will be ignored. Current value: bagging_freq=3
[LightGBM] [Warning] lambda_l2 is set=3.9692659066748037, reg_lamb

/usr/local/lib/python3.10/dist-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.10/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "
[I 2024-08-28 02:24:16,353] Trial 0 finished with value: 0.8891564078606372 and parameters: {'lambda_l1': 2.3639511783118508, 'lambda_l2': 3.9692659066748037, 'num_leaves': 50, 'feature_fraction': 0.770150279456767, 'bagging_fraction': 0.8702645753942929, 'bagging_freq': 3, 'min_child_samples': 76, 'l

...

[LightGBM] [Warning] feature_fraction is set=0.7108259223633461, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7108259223633461
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] lambda_l2 is set=1.6904693429923399, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.6904693429923399
[LightGBM] [Warning] bagging_fraction is set=0.981317846545809, subsample=1.0 will be ignored. Current value: bagging_fraction=0.981317846545809
[LightGBM] [Warning] lambda_l1 is set=1.797389568818884, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.797389568818884


/usr/local/lib/python3.10/dist-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/usr/local/lib/python3.10/dist-packages/lightgbm/sklearn.py:736: UserWarning: 'verbose' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose' argument is deprecated and will be removed in a future release of LightGBM. "


[LightGBM] [Warning] feature_fraction is set=0.7108259223633461, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7108259223633461
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] lambda_l2 is set=1.6904693429923399, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.6904693429923399
[LightGBM] [Warning] bagging_fraction is set=0.981317846545809, subsample=1.0 will be ignored. Current value: bagging_fraction=0.981317846545809
[LightGBM] [Warning] lambda_l1 is set=1.797389568818884, reg_alpha=0.0 will be ignored. Current value: lambda_l1=1.797389568818884


[I 2024-08-28 02:40:02,554] Trial 99 finished with value: 0.860010734936056 and parameters: {'lambda_l1': 1.797389568818884, 'lambda_l2': 1.6904693429923399, 'num_leaves': 108, 'feature_fraction': 0.7108259223633461, 'bagging_fraction': 0.981317846545809, 'bagging_freq': 6, 'min_child_samples': 9, 'learning_rate': 0.08940136824374516}. Best is trial 46 with value: 0.8736279628453424.


Best params for 1f_ele: {'lambda_l1': 0.851682830939924, 'lambda_l2': 2.491770059953741, 'num_leaves': 96, 'feature_fraction': 0.9886649743714837, 'bagging_fraction': 0.9698805910945327, 'bagging_freq': 7, 'min_child_samples': 5, 'learning_rate': 0.08554624068287443}
[LightGBM] [Warning] lambda_l1 is set=0.851682830939924, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.851682830939924
[LightGBM] [Warning] feature_fraction is set=0.9886649743714837, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9886649743714837
[LightGBM] [Warning] bagging_freq is set=7, subsample_freq=0 will be ignored. Current value: bagging_freq=7
[LightGBM] [Warning] lambda_l2 is set=2.491770059953741, reg_lambda=0.0 will be ignored. Current value: lambda_l2=2.491770059953741
[LightGBM] [Warning] bagging_fraction is set=0.9698805910945327, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9698805910945327
Model saved as: /content/drive/MyDrive/practce/1f_ele_model_

In [ ]:
# 예측 데이터
future_data = pd.DataFrame({
    'date': ['7/15/2025'],
    'time': ['18:30'],
})

future_data['datetime'] = pd.to_datetime(future_data['date'] + ' ' + future_data['time'])
future_data['year'] = future_data['datetime'].dt.year
future_data['month'] = future_data['datetime'].dt.month
future_data['day'] = future_data['datetime'].dt.day
future_data['hour'] = future_data['datetime'].dt.hour
future_data['dayofweek'] = future_data['datetime'].dt.dayofweek
future_X = future_data[['year', 'month', 'day', 'hour', 'dayofweek']]

In [ ]:
# 예측 데이터
future_data = pd.DataFrame({
    'date': ['6/15/2025'],
    'time': ['13:30'],
})

future_data['datetime'] = pd.to_datetime(future_data['date'] + ' ' + future_data['time'])
future_data['year'] = future_data['datetime'].dt.year
future_data['month'] = future_data['datetime'].dt.month
future_data['day'] = future_data['datetime'].dt.day
future_data['hour'] = future_data['datetime'].dt.hour
future_data['dayofweek'] = future_data['datetime'].dt.dayofweek
future_X = future_data[['year', 'month', 'day', 'hour', 'dayofweek']]

# 예측 결과 출력
def load_and_predict(target_column, future_X):
    model_filename = "/content/drive/MyDrive/practce/" + f"{target_column}_model_final.pkl"
    model = joblib.load(model_filename)
    prediction = model.predict(future_X)
    print(f"Loaded model for {target_column} predicts: {prediction[0]}")

print("\nLoading models and making predictions:")
for target_column in target_columns:
    load_and_predict(target_column, future_X)


Loading models and making predictions:
Loaded model for 1f_1 predicts: 218.06935910307453
Loaded model for 1f_but predicts: 133.03117814094682
Loaded model for 2f_he predicts: 146.74762124007333
Loaded model for 2f_2 predicts: 80.88200906399489
Loaded model for 1f_ele predicts: 30.053989099264573


In [ ]:
def evaluate_model(target_column):
    y = data[target_column]

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    #model_filename = "/content/drive/MyDrive/practce/" + f"{target_column}_model.pkl"
    model_filename = "/content/drive/MyDrive/practce/" + f"{target_column}_model_final.pkl"
    model = joblib.load(model_filename)

    y_pred = model.predict(X_test)

    r2 = r2_score(y_test, y_pred)
    print(f"{target_column} - Test R² score: {r2}")

    return r2

r2_scores = {}
for target_column in target_columns:
    print(f"Evaluating model for {target_column}")
    r2_scores[target_column] = evaluate_model(target_column)

print("\nR² scores for each loaded model:")
for target_column, r2 in r2_scores.items():
    print(f"{target_column}: R² score = {r2}")

Evaluating model for 1f_1
1f_1 - Test R² score: 0.9288393438695912
Evaluating model for 1f_but
1f_but - Test R² score: 0.9241982131308304
Evaluating model for 2f_he
2f_he - Test R² score: 0.9365206165261238
Evaluating model for 2f_2
2f_2 - Test R² score: 0.9083168390269308
Evaluating model for 1f_ele
1f_ele - Test R² score: 0.875645300596796

R² scores for each loaded model:
1f_1: R² score = 0.9288393438695912
1f_but: R² score = 0.9241982131308304
2f_he: R² score = 0.9365206165261238
2f_2: R² score = 0.9083168390269308
1f_ele: R² score = 0.875645300596796
